In [4]:
import pandas as pd
import numpy as np
import time
from datetime import datetime, timedelta
from bisect import insort_left,insort_right
from tabulate import tabulate
import random
from random import randint
import os

In [5]:
def check_arrival_time(jobs,start_time, last_check_time):
    current_time = datetime.now()
    elapsed_seconds = (current_time - start_time).total_seconds()

    new_arrivals = []
    if last_check_time==0: 
        for idx, job in enumerate(jobs):
            if job.release <= elapsed_seconds:
                new_arrivals.append(idx)
    else: 
        for idx, job in enumerate(jobs):
        #print("elapsed_seconds", elapsed_seconds, "last_check_time", last_check_time)
            if job.release <= elapsed_seconds  and job.release > last_check_time:
                new_arrivals.append(idx)

    return new_arrivals

In [58]:
def run_one(jobs, m,RANDOM_alpha,RANDOM_assigment,alpha,time_step):
    np.random.seed(10)

    # List to store arrived jobs
    L = []
    machines=np.zeros(m)
    for job in jobs: job.done_1=0
    ite=0
  
        

    # Initialize last check time
    relative_current = 0
    # Record the starting time of the algorithm
    start_time = datetime.now()
    
    # Check for arrival time every 1 second
    while sum(job.done_1 for job in jobs)<len(jobs):
        ite=ite+1
        new_arrivals = check_arrival_time(jobs,start_time, relative_current)
        # Update last check time
        relative_current = (datetime.now() - start_time).total_seconds()
        if Printing:
            if not new_arrivals:     
                print("\n\n NEW ITERATION")
                print("not new")
        #update L if new job arrived 
        for arrived_job_idx in new_arrivals:
            arrived_job = jobs[arrived_job_idx]
            arrived_job.done_1=0
            arrived_job.MBT=0
            if Printing: 
                print("\n\n NEW ITERATION")
                print(f"One job arrived at {datetime.now()} for {arrived_job.id}")

            ##MODYFY TO have 50 different cases for reproducibility
            if RANDOM_alpha: 
                arrived_job.alpha=np.random.uniform(0,1)
            else:
                arrived_job.alpha=alpha #MODYFY BASED  ON RSOS OR DSOS
            insort_right(L, arrived_job, key=lambda x: -(x.we/x.expected))

            #current_time = datetime.now()
            #relative_current=(current_time-start_time).total_seconds()

    
        #process first job in L
        if L:
            #print("list not empty")
            #print("start",len(L),L)
            remaning=(1-L[0].done_1)*L[0].expected/m 
            #print("for job::",L[0].id,"done:", L[0].done_1, "remaning:",remaning)
            #print("L",L, len(L))
            i=0
            tot=0
            while tot+remaning<=time_step and i <len(L):

                #L[i].MBT=L[i].MBT+(m/L[i].expected)*((current_time+timedelta(seconds=tot+remaning)).timestamp()**2-(current_time+timedelta(seconds=tot)).timestamp()**2)#correct
                #L[i].MBT=L[i].MBT+(m/L[i].expected)*((current_time-start_time+timedelta(seconds=tot+remaning)).total_seconds()**2-(current_time-start_time+timedelta(seconds=tot)).total_seconds()**2)
                L[i].MBT=L[i].MBT+(m/L[i].expected)*(remaning*(2*(tot+relative_current) +remaning))/2 # (relative_curreny+tot+remaing)^2-(relative_curreny+tot)^2
                if L[i].done_1< L[i].alpha:
                    L[i].ta=relative_current+tot+(L[i].alpha-L[i].done_1)*L[i].expected/m
                    if RANDOM_assigment: machine=randint(0,m-1)
                    else: 
                        minimum_load=np.min(machines)
                        machine=np.min(np.where(machines==minimum_load))
                        #machine=machines.index(min(machines))
                    if machines[machine]>=L[i].ta:
                        machines[machine]=machines[machine]+L[i].processing
                    else:
                        machines[machine]=L[i].ta+L[i].processing
                    L[i].complition=machines[machine]

                L[i].done_1=1
                #current_time=current_time+(1-L[i].done_1)*L[i].expected/m 
                i=i+1
                tot=tot+remaning
                if len(L)>i:
                    remaning=(1-L[i].done_1)*L[i].expected/m 

            if len(L)>i:
                #print("i:" ,i ,"tot",tot )

                done_before=L[i].done_1    
                L[i].done_1=L[i].done_1+(time_step-tot)/(L[i].expected/m)
                #print('start',start,'end_time',end_time)
                #L[i].MBT=L[i].MBT+(m/L[i].expected)*((current_time+timedelta(seconds=time_step))**2-(current_time+timedelta(seconds=tot))**2)
                #L[i].MBT=L[i].MBT+(m/L[i].expected)*((end_time.timestamp())**2-(start.timestamp())**2)#correct
                #print("MBT", L[i].id,"before",L[i].MBT,"summed",(end_time**2-start**2),"after",L[i].MBT+(end_time**2-start**2))
                if done_before< L[i].alpha<=L[i].done_1:
                    L[i].ta=relative_current+tot+(L[i].alpha-done_before)*L[i].expected/m 
                    if RANDOM_assigment: machine=randint(0,m-1)
                    else: 
                        minimum_load=np.min(machines)
                        machine=np.min(np.where(machines==minimum_load))
                    if machines[machine]>=L[i].ta:
                        machines[machine]=machines[machine]+L[i].processing
                    else:
                        machines[machine]=L[i].ta+L[i].processing
                    L[i].complition=machines[machine]
                L[i].MBT=L[i].MBT+(m/L[i].expected)*((relative_current+ time_step)**2-(relative_current+ tot)**2)/2
                #print("END","for job::",L[0].id,"done:", L[0].done_1, "remaning:",(1-L[0].done_1)*L[0].expected/m )
                L=L[i:]

            else: 
                L=[]
            

    # Print the table
        if Printing:
            #check alpha_point to see if it enters other list 
            table_data = [(job.id, job.release, job.done_1, (1-job.done_1)*job.expected/m, job.MBT , job.ta, job.processing, job.complition, job.alpha) for job in jobs]
            print("end",len(L),L)
            print("after iteration:", ite, "and time:", (datetime.now() - start_time).total_seconds())
            print(tabulate(table_data, headers=['Job ID','release', 'Done', 'Remaining', 'Mean busy time','alpha_point', 'processing','complition', 'alpha']))
            print(machines)


        time.sleep(time_step)  # sleep for 1 second
    total_complition = sum(job.we * job.complition for job in jobs)
    total_LR= sum(job.we * (job.MBT-(job.CV-1)*job.expected/2) for job in jobs)
    return total_complition, total_LR

In [16]:
def run_one_both(jobs, m,alpha,time_step):
    #np.random.seed(10)

    # List to store arrived jobs
    L=[]
    upper_time=max(job.release for job in jobs)+sum(job.expected for job in jobs)
    machines_DSOS=np.zeros(m)
    machines_RSOS=np.zeros(m)
    ite=0
    for job in jobs: job.done_1=0

    # Initialize last check time
    relative_current = 0
    # Record the starting time of the algorithm
    start_time = datetime.now()
    

    # Check for arrival time every 1 second
    while sum(job.done_1 for job in jobs)<len(jobs):
        ite=ite+1
        if ite%10==0: print("iteration",ite)
        new_arrivals = check_arrival_time(jobs,start_time, relative_current)
        # Update last check time
        relative_current = (datetime.now() - start_time).total_seconds()
        if Printing:
            if not new_arrivals:     
                print("\n\n NEW ITERATION")
                print("not new")
        #update L if new job arrived 
        for arrived_job_idx in new_arrivals:
            arrived_job = jobs[arrived_job_idx]
            #arrived_job.done_1=0
            arrived_job.MBT=0
            if Printing: 
                print("\n\n NEW ITERATION")
                print(f"One job arrived at {datetime.now()} for {arrived_job.id}")

            ##MODYFY TO have 50 different cases for reproducibility
            #if RANDOM_alpha: 
             #   arrived_job.alpha=np.random.uniform(0,1)
            #else:
             #   arrived_job.alpha=alpha #MODYFY BASED  ON RSOS OR DSOS
            
            arrived_job.alpha_RSOS=np.random.uniform(0,1)
            #else:
            arrived_job.alpha_DSOS=alpha #MODYFY BASED  ON RSOS OR DSOS
            insort_right(L, arrived_job, key=lambda x: -(x.we/x.expected))

            #current_time = datetime.now()
            #relative_current=(current_time-start_time).total_seconds()

    
        #process first job in L
        if L:
            #print("list not empty")
            #print("start",len(L),L)
            remaning=(1-L[0].done_1)*L[0].expected/m 
            #print("for job::",L[0].id,"done:", L[0].done_1, "remaning:",remaning)
            #print("L",L, len(L))
            i=0
            tot=0
            while tot+remaning<=time_step and i <len(L):

                #L[i].MBT=L[i].MBT+(m/L[i].expected)*((current_time+timedelta(seconds=tot+remaning)).timestamp()**2-(current_time+timedelta(seconds=tot)).timestamp()**2)#correct
                #L[i].MBT=L[i].MBT+(m/L[i].expected)*((current_time-start_time+timedelta(seconds=tot+remaning)).total_seconds()**2-(current_time-start_time+timedelta(seconds=tot)).total_seconds()**2)
                L[i].MBT=L[i].MBT+(m/L[i].expected)*(remaning*(2*(tot+relative_current) +remaning))/2 # (relative_curreny+tot+remaing)^2-(relative_curreny+tot)^2
                if L[i].done_1< L[i].alpha_RSOS:
                    L[i].ta_RSOS=relative_current+tot+(L[i].alpha_RSOS-L[i].done_1)*L[i].expected/m
                    machine=randint(0,m-1) 
                        #machine=machines.index(min(machines))
                    if machines_RSOS[machine]>=L[i].ta_RSOS:
                        machines_RSOS[machine]=machines_RSOS[machine]+L[i].processing
                    else:
                        machines_RSOS[machine]=L[i].ta_RSOS+L[i].processing
                    L[i].comp_RSOS=machines_RSOS[machine]
                    
                if L[i].done_1< L[i].alpha_DSOS:
                    L[i].ta_DSOS=relative_current+tot+(L[i].alpha_DSOS-L[i].done_1)*L[i].expected/m
                    minimum_load=np.min(machines_DSOS)
                    machine=np.min(np.where(machines_DSOS==minimum_load))
                        #machine=machines.index(min(machines))
                    if machines_DSOS[machine]>=L[i].ta_DSOS:
                        machines_DSOS[machine]=machines_DSOS[machine]+L[i].processing
                    else:
                        machines_DSOS[machine]=L[i].ta_DSOS+L[i].processing
                    L[i].comp_DSOS=machines_DSOS[machine]

                L[i].done_1=1
                #current_time=current_time+(1-L[i].done_1)*L[i].expected/m 
                i=i+1
                tot=tot+remaning
                if len(L)>i:
                    remaning=(1-L[i].done_1)*L[i].expected/m 

            if len(L)>i:
                #print("i:" ,i ,"tot",tot )

                done_before=L[i].done_1    
                L[i].done_1=L[i].done_1+(time_step-tot)/(L[i].expected/m)
                #print('start',start,'end_time',end_time)
                #L[i].MBT=L[i].MBT+(m/L[i].expected)*((current_time+timedelta(seconds=time_step))**2-(current_time+timedelta(seconds=tot))**2)
                #L[i].MBT=L[i].MBT+(m/L[i].expected)*((end_time.timestamp())**2-(start.timestamp())**2)#correct
                #print("MBT", L[i].id,"before",L[i].MBT,"summed",(end_time**2-start**2),"after",L[i].MBT+(end_time**2-start**2))
                if done_before< L[i].alpha_RSOS<=L[i].done_1:
                    L[i].ta_RSOS=relative_current+tot+(L[i].alpha_RSOS-done_before)*L[i].expected/m 
                    machine=randint(0,m-1)
                    if machines_RSOS[machine]>=L[i].ta_RSOS:
                        machines_RSOS[machine]=machines_RSOS[machine]+L[i].processing
                    else:
                        machines_RSOS[machine]=L[i].ta_RSOS+L[i].processing
                    L[i].comp_RSOS=machines_RSOS[machine]
                if done_before< L[i].alpha_DSOS<=L[i].done_1:
                    L[i].ta_DSOS=relative_current+tot+(L[i].alpha_DSOS-done_before)*L[i].expected/m  
                    minimum_load=np.min(machines_DSOS)
                    machine=np.min(np.where(machines_DSOS==minimum_load))
                    if machines_DSOS[machine]>=L[i].ta_DSOS:
                        machines_DSOS[machine]=machines_DSOS[machine]+L[i].processing
                    else:
                        machines_DSOS[machine]=L[i].ta_DSOS+L[i].processing
                    L[i].comp_DSOS=machines_DSOS[machine]
                    
                    
                    
                L[i].MBT=L[i].MBT+(m/L[i].expected)*((relative_current+ time_step)**2-(relative_current+ tot)**2)/2
                #print("END","for job::",L[0].id,"done:", L[0].done_1, "remaning:",(1-L[0].done_1)*L[0].expected/m )
                L=L[i:]

            else: 
                L=[]
            

    # Print the table
        if Printing:
            #check alpha_point to see if it enters other list 
            table_data = [(job.id, job.release, job.done_1, (1-job.done_1)*job.expected/m, job.MBT , job.processing, job.alpha_RSOS, job.ta_RSOS, job.alpha_DSOS, job.ta_DSOS, job.comp_RSOS, job.comp_DSOS) for job in jobs]
            print("end",len(L),L)
            print("after iteration:", ite, "and time:", (datetime.now() - start_time).total_seconds())
            print(tabulate(table_data, headers=['Job ID','release', 'Done', 'Remaining', 'Mean busy time','processing','alpha_R','alpha_point_R','alpha_D','alpha_point_D','complition_R', 'complition_D']))
            print("RSOS",machines_RSOS)
            print("DSOS",machines_DSOS)


        time.sleep(time_step)  # sleep for 1 second
    total_comp_RSOS = sum(job.we * job.comp_RSOS for job in jobs)
    total_comp_DSOS = sum(job.we * job.comp_DSOS for job in jobs)
    total_LR= sum(job.we * (job.MBT-(job.CV-1)*job.expected/2) for job in jobs)
    return total_comp_RSOS,total_comp_DSOS, total_LR

In [11]:
class Job:
    def __init__(self, job_id, release,expected,CV, weigth,processing=0,alpha=None,MBT=0):
        # information needed for single machine: id, release, expected processing time, weigths
        self.id = job_id
        self.release = release
        self.processing = processing
        self.expected=expected
        self.CV=CV
        self.we=weigth
        self.alpha=None
        self.ta=None
        self.done_1=0
        self.MBT=0
        self.complition=0
        

In [61]:
def check_arrival_time_fast(jobs,last_check_time,current_time):
    #print("last_check_time,current_time",last_check_time,current_time,)
   # current_time = datetime.now()
    #elapsed_seconds = (current_time - start_time).total_seconds()

    new_arrivals = []
    if current_time==0: 
        for idx, job in enumerate(jobs):
            if job.release <= 0:
                new_arrivals.append(idx)
    else: 
        for idx, job in enumerate(jobs):
        #print("elapsed_seconds", elapsed_seconds, "last_check_time", last_check_time)
            if job.release <= current_time  and job.release > last_check_time:
                new_arrivals.append(idx)

    return new_arrivals

def run_one_both_fast(jobs, m,alpha):
    #np.random.seed(10)
    upper_time=max(job.release for job in jobs)+sum(job.expected for job in jobs)
    #semplify arrival times
    Arrivals=[job.release for job in jobs]
    
    arrival=1
    Arrivals=list(set(Arrivals))
    Arrivals.sort()
    Arrivals.append(upper_time)
    if Arrivals[0]!=0: Arrivals.insert(0,0)
    #print(Arrivals)
    # List to store arrived jobs
    L=[]
    #upper_time=max(job.release for job in jobs)+sum(job.expected for job in jobs)
    machines_DSOS=np.zeros(m)
    machines_RSOS=np.zeros(m)
    ite=0
    for job in jobs: job.done_1=0

    # Initialize last check time
    relative_current = 0
    #current_time=0
    last_check_time=0
    # Record the starting time of the algorithm
    
    

    # Check for arrival time every 1 second
    while sum(job.done_1 for job in jobs)<len(jobs):
        time_step=Arrivals[arrival]-Arrivals[arrival-1]
        arrival=arrival+1
        ite=ite+1
        if ite%10==0: print("iteration",ite)
        new_arrivals = check_arrival_time_fast(jobs,last_check_time, relative_current)
        last_check_time=relative_current
        # Update last check time
        #relative_current = (datetime.now() - start_time).total_seconds()
        if Printing:
            if not new_arrivals:     
                print("\n\n NEW ITERATION")
                print("not new")
        #update L if new job arrived 
        for arrived_job_idx in new_arrivals:
            arrived_job = jobs[arrived_job_idx]
            #arrived_job.done_1=0
            arrived_job.MBT=0
            if Printing: 
                print("\n\n NEW ITERATION")
                print(f"One job arrived at {relative_current} for {arrived_job.id}")

            ##MODYFY TO have 50 different cases for reproducibility
            #if RANDOM_alpha: 
             #   arrived_job.alpha=np.random.uniform(0,1)
            #else:
             #   arrived_job.alpha=alpha #MODYFY BASED  ON RSOS OR DSOS
            
            arrived_job.alpha_RSOS=np.random.uniform(0,1)
            #else:
            arrived_job.alpha_DSOS=alpha #MODYFY BASED  ON RSOS OR DSOS
            insort_right(L, arrived_job, key=lambda x: -(x.we/x.expected))

            #current_time = datetime.now()
            #relative_current=(current_time-start_time).total_seconds()

    
        #process first job in L
        if L:
            #print("list not empty")
            #print("start",len(L),L)
            remaning=(1-L[0].done_1)*L[0].expected/m 
            #print("for job::",L[0].id,"done:", L[0].done_1, "remaning:",remaning)
            #print("L",L, len(L))
            i=0
            tot=0
            while tot+remaning<=time_step and i <len(L):

                #L[i].MBT=L[i].MBT+(m/L[i].expected)*((current_time+timedelta(seconds=tot+remaning)).timestamp()**2-(current_time+timedelta(seconds=tot)).timestamp()**2)#correct
                #L[i].MBT=L[i].MBT+(m/L[i].expected)*((current_time-start_time+timedelta(seconds=tot+remaning)).total_seconds()**2-(current_time-start_time+timedelta(seconds=tot)).total_seconds()**2)
                L[i].MBT=L[i].MBT+(m/L[i].expected)*(remaning*(2*(tot+relative_current) +remaning))/2 # (relative_curreny+tot+remaing)^2-(relative_curreny+tot)^2
                if L[i].done_1< L[i].alpha_RSOS:
                    L[i].ta_RSOS=relative_current+tot+(L[i].alpha_RSOS-L[i].done_1)*L[i].expected/m
                    machine=randint(0,m-1) 
                        #machine=machines.index(min(machines))
                    if machines_RSOS[machine]>=L[i].ta_RSOS:
                        machines_RSOS[machine]=machines_RSOS[machine]+L[i].processing
                    else:
                        machines_RSOS[machine]=L[i].ta_RSOS+L[i].processing
                    L[i].comp_RSOS=machines_RSOS[machine]
                    
                if L[i].done_1< L[i].alpha_DSOS:
                    L[i].ta_DSOS=relative_current+tot+(L[i].alpha_DSOS-L[i].done_1)*L[i].expected/m
                    minimum_load=np.min(machines_DSOS)
                    machine=np.min(np.where(machines_DSOS==minimum_load))
                        #machine=machines.index(min(machines))
                    if machines_DSOS[machine]>=L[i].ta_DSOS:
                        machines_DSOS[machine]=machines_DSOS[machine]+L[i].processing
                    else:
                        machines_DSOS[machine]=L[i].ta_DSOS+L[i].processing
                    L[i].comp_DSOS=machines_DSOS[machine]

                L[i].done_1=1
                #current_time=current_time+(1-L[i].done_1)*L[i].expected/m 
                i=i+1
                tot=tot+remaning
                if len(L)>i:
                    remaning=(1-L[i].done_1)*L[i].expected/m 

            if len(L)>i:
                #print("i:" ,i ,"tot",tot )

                done_before=L[i].done_1    
                L[i].done_1=L[i].done_1+(time_step-tot)/(L[i].expected/m)
                #print('start',start,'end_time',end_time)
                #L[i].MBT=L[i].MBT+(m/L[i].expected)*((current_time+timedelta(seconds=time_step))**2-(current_time+timedelta(seconds=tot))**2)
                #L[i].MBT=L[i].MBT+(m/L[i].expected)*((end_time.timestamp())**2-(start.timestamp())**2)#correct
                #print("MBT", L[i].id,"before",L[i].MBT,"summed",(end_time**2-start**2),"after",L[i].MBT+(end_time**2-start**2))
                if done_before< L[i].alpha_RSOS<=L[i].done_1:
                    L[i].ta_RSOS=relative_current+tot+(L[i].alpha_RSOS-done_before)*L[i].expected/m 
                    machine=randint(0,m-1)
                    if machines_RSOS[machine]>=L[i].ta_RSOS:
                        machines_RSOS[machine]=machines_RSOS[machine]+L[i].processing
                    else:
                        machines_RSOS[machine]=L[i].ta_RSOS+L[i].processing
                    L[i].comp_RSOS=machines_RSOS[machine]
                if done_before< L[i].alpha_DSOS<=L[i].done_1:
                    L[i].ta_DSOS=relative_current+tot+(L[i].alpha_DSOS-done_before)*L[i].expected/m  
                    minimum_load=np.min(machines_DSOS)
                    machine=np.min(np.where(machines_DSOS==minimum_load))
                    if machines_DSOS[machine]>=L[i].ta_DSOS:
                        machines_DSOS[machine]=machines_DSOS[machine]+L[i].processing
                    else:
                        machines_DSOS[machine]=L[i].ta_DSOS+L[i].processing
                    L[i].comp_DSOS=machines_DSOS[machine]
                    
                    
                    
                L[i].MBT=L[i].MBT+(m/L[i].expected)*((relative_current+ time_step)**2-(relative_current+ tot)**2)/2
                #print("END","for job::",L[0].id,"done:", L[0].done_1, "remaning:",(1-L[0].done_1)*L[0].expected/m )
                L=L[i:]

            else: 
                L=[]
            
            
        relative_current= relative_current + time_step # sleep for 1 second
    # Print the table
        if Printing:
            #check alpha_point to see if it enters other list 
            table_data = [(job.id, job.release, job.done_1, (1-job.done_1)*job.expected/m, job.MBT , job.processing, job.alpha_RSOS, job.ta_RSOS, job.alpha_DSOS, job.ta_DSOS, job.comp_RSOS, job.comp_DSOS) for job in jobs]
            print("end",len(L),L)
            print("after iteration:", ite, "and time:", relative_current)
            print(tabulate(table_data, headers=['Job ID','release', 'Done', 'Remaining', 'Mean busy time','processing','alpha_R','alpha_point_R','alpha_D','alpha_point_D','complition_R', 'complition_D']))
            print("RSOS",machines_RSOS)
            print("DSOS",machines_DSOS)


        
    total_comp_RSOS = sum(job.we * job.comp_RSOS for job in jobs)
    total_comp_DSOS = sum(job.we * job.comp_DSOS for job in jobs)
    total_LR= sum(job.we * (job.MBT-(job.CV-1)*job.expected/2) for job in jobs)
    return total_comp_RSOS,total_comp_DSOS, total_LR

In [56]:
jobs_data = [
    {'job_id': '1', 'release': 4, 'processing': 5, 'expected': 4.5, 'CV':3,'weigth':4.5},
    {'job_id': '2', 'release': 1, 'processing': 3,'expected': 3, 'CV':0,'weigth':3},
    {'job_id': '3', 'release': 3, 'processing': 5,'expected': 1.5, 'CV':1,'weigth':1.5},
    {'job_id': '4', 'release': 5, 'processing': 3,'expected': 3, 'CV':1,'weigth':3},
    {'job_id': '5', 'release': 4, 'processing': 5, 'expected': 4.5, 'CV':3,'weigth':4.5},
    {'job_id': '6', 'release': 10, 'processing': 3,'expected': 3, 'CV':0,'weigth':3},
    #{'job_id': '5', 'release': 9, 'processing': 5,'expected': 1.5, 'CV':4,'weigth':1.5},
    #{'job_id': '6', 'release': 5, 'processing': 3,'expected': 3, 'CV':1,'weigth':3},
    #{'job_id': '7', 'release': 7, 'processing': 5,'expected': 1.5, 'CV':4,'weigth':1.5}


]
#convert list to list of object
jobs = [Job_b(**job_data) for job_data in jobs_data]

In [57]:
m=3
alpha=0.5
Printing=True
jobs_after=run_one_both_fast(jobs, m,alpha)

[0, 1, 3, 4, 5, 10, 29.5]
last_check_time,current_time 0 0


 NEW ITERATION
not new
end 0 []
after iteration: 1 and time: 1
  Job ID    release    Done    Remaining    Mean busy time    processing  alpha_R    alpha_point_R    alpha_D    alpha_point_D      complition_R    complition_D
--------  ---------  ------  -----------  ----------------  ------------  ---------  ---------------  ---------  ---------------  --------------  --------------
       1          4       0          1.5                 0             5                                                                       0               0
       2          1       0          1                   0             3                                                                       0               0
       3          3       0          0.5                 0             5                                                                       0               0
       4          5       0          1                   0             

In [49]:
class Job_b:
    def __init__(self, job_id, release, expected,CV, weigth,processing=0,alpha=None,MBT=0):
        # information needed for single machine: id, release, expected processing time, weigths
        self.id = job_id
        self.release = release
        self.processing = processing
        self.expected=expected
        self.CV=CV
        self.we=weigth
        self.alpha_RSOS=None
        self.alpha_DSOS=None
        self.ta_RSOS=None
        self.ta_DSOS=None
        self.done_1=0
        self.MBT=0
        self.comp_RSOS=0
        self.comp_DSOS=0


In [65]:
np.random.seed(10)
random.seed(10)
instances=50
realizations_p=50
n=1000
m=3
time_step=1
Printing=False
function="fun"


name=f"results_m_{m}_n_{n}_fun_{function}.csv"
#df_name=f"df_m_{m}"
#globals()[df_name]=df

results=[]
for i in range(instances):
    print("-------------------------------------------------------------------------------------------")
    print("------------------------------------------------NEW istance---------------------------------")
    print("-------------------------------------------------------------------------------------------")
    Jobs=[]
    result_istance=[]
    for x in range(n):
        expected=randint(1,20)
        release=randint(0,round(n*5))
        CV=1/3
        we=random.uniform(0, 30)
        job=Job_b(x,release,expected,CV,we)
        Jobs.append(job)
    for j in range(realizations_p):
        for k in range(n): Jobs[k].processing=np.random.uniform(0,2*Jobs[k].expected)
        print("------------------------------------------------NEW Processing---------------------------------")
        print("-------------------------------------------------------------------------------------------")
        #[print(vars(job)) for job in Jobs]
        alpha=0.5
        total_RSOS,total_DSOS,total_LR=run_one_both_fast(Jobs,m,alpha)
        print("for istance",i,"realization",j,total_RSOS,total_DSOS,total_LR)
        result_istance.append([total_RSOS,total_DSOS,total_LR])
    results.append(result_istance)
    
directory_path= os.path.join('results',function,'m_'+str(m))
name=f"results_m_{m}_n_{n}_{function}.csv"
file_path = os.path.join(directory_path, name)
if not os.path.exists(directory_path):
    # Create the directory if it doesn't exist
    os.makedirs(directory_path)
df=pd.DataFrame(results)
df.to_csv(file_path,index=False)
            #processing=
            #create job
    #run_one for each row
    

-------------------------------------------------------------------------------------------
------------------------------------------------NEW istance---------------------------------
-------------------------------------------------------------------------------------------
------------------------------------------------NEW Processing---------------------------------
-------------------------------------------------------------------------------------------
iteration 10
iteration 20
iteration 30
iteration 40
iteration 50
iteration 60
iteration 70
iteration 80
iteration 90
iteration 100
iteration 110
iteration 120
iteration 130
iteration 140
iteration 150
iteration 160
iteration 170
iteration 180
iteration 190
iteration 200
iteration 210
iteration 220
iteration 230
iteration 240
iteration 250
iteration 260
iteration 270
iteration 280
iteration 290
iteration 300
iteration 310
iteration 320
iteration 330
iteration 340
iteration 350
iteration 360
iteration 370
iteration 380
iteration 39

In [100]:
np.random.seed(10)
random.seed(10)
instances=50
realizations_p=50
n=10
m=2
time_step=1
Printing=False
function="fun"


name=f"results_m_{m}_n_{n}_fun_{function}.csv"
#df_name=f"df_m_{m}"
#globals()[df_name]=df

results=[]
for i in range(instances):
    print("-------------------------------------------------------------------------------------------")
    print("------------------------------------------------NEW istance---------------------------------")
    print("-------------------------------------------------------------------------------------------")
    Jobs=[]
    result_istance=[]
    for x in range(n):
        expected=randint(1,50)
        release=randint(0,round(n*50/2))
        CV=1/3
        we=random.uniform(0, 30)
        job=Job(x,release,expected,CV,we)
        Jobs.append(job)
    for j in range(realizations_p):
        for k in range(n): Jobs[k].processing=np.random.uniform(0,2*Jobs[k].expected)
        print("------------------------------------------------NEW Processing---------------------------------")
        print("-------------------------------------------------------------------------------------------")
        [print(vars(job)) for job in Jobs]
        RANDOM_alpha=True
        RANDOM_assigment=True
        alpha=0
        total_RSOS,total_LR_RSOS=run_one(Jobs,m,RANDOM_alpha,RANDOM_assigment,alpha,time_step)
        print("-----------------------------------------------------------DSOS---------------------------------------------------------------------------")
        [print(vars(job)) for job in Jobs]
        RANDOM_alpha=False
        RANDOM_assigment=False
        alpha=0.5
        total_DSOS, total_LR_DSOS=run_one(Jobs,m,RANDOM_alpha,RANDOM_assigment,alpha,time_step)
        print("for istance",i,"realization",j,total_RSOS,total_DSOS,total_LR_RSOS,total_LR_DSOS)
        result_istance.append([total_RSOS,total_DSOS,total_LR_RSOS])
    results.append(result_istance)
    
directory_path= os.path.join('results',function,'m_'+str(m))
name=f"results_m_{m}_n_{n}_{function}.csv"
file_path = os.path.join(directory_path, name)
if not os.path.exists(directory_path):
    # Create the directory if it doesn't exist
    os.makedirs(directory_path)
df=pd.DataFrame(results)
df.to_csv(file_path,index=False)
            #processing=
            #create job
    #run_one for each row
    

-------------------------------------------------------------------------------------------
------------------------------------------------NEW istance---------------------------------
-------------------------------------------------------------------------------------------
------------------------------------------------NEW Processing---------------------------------
-------------------------------------------------------------------------------------------
{'id': 0, 'release': 8, 'processing': 57.077727601739205, 'expected': 37, 'CV': 0.3333333333333333, 'we': 12.866671640253438, 'alpha': None, 'ta': None, 'done_1': 0, 'MBT': 0, 'complition': 0}
{'id': 1, 'release': 3, 'processing': 1.535644252595711, 'expected': 37, 'CV': 0.3333333333333333, 'we': 6.182946964185052, 'alpha': None, 'ta': None, 'done_1': 0, 'MBT': 0, 'complition': 0}
{'id': 2, 'release': 210, 'processing': 40.55348703528163, 'expected': 32, 'CV': 0.3333333333333333, 'we': 8.325619843633293, 'alpha': None, 'ta': None

KeyboardInterrupt: 

In [ ]:
results

In [95]:

directory_path= os.path.join('results',function,'m_'+str(m))
name=f"results_m_{m}_n_{n}_{function}.csv"
file_path = os.path.join(directory_path, name)
if not os.path.exists(directory_path):
    # Create the directory if it doesn't exist
    os.makedirs(directory_path)
df=pd.DataFrame(results)
df.to_csv(file_path,index=False)

In [105]:
max(job.release for job in Jobs)+sum(job.expected for job in Jobs)

469

In [106]:
max(job.complition for job in Jobs)

258.6256800352816

In [32]:
[print(vars(job)) for job in Jobs]

{'id': 0, 'release': 2, 'processing': 0, 'expected': 1, 'CV': 1, 'we': 3, 'alpha': None, 'ta': None, 'done_1': 0, 'MBT': 0, 'complition': 0}
{'id': 1, 'release': 3, 'processing': 1, 'expected': 3, 'CV': 1, 'we': 0, 'alpha': None, 'ta': None, 'done_1': 0, 'MBT': 0, 'complition': 0}
{'id': 2, 'release': 1, 'processing': 1, 'expected': 2, 'CV': 1, 'we': 1, 'alpha': None, 'ta': None, 'done_1': 0, 'MBT': 0, 'complition': 0}
{'id': 3, 'release': 1, 'processing': 2, 'expected': 3, 'CV': 1, 'we': 0, 'alpha': None, 'ta': None, 'done_1': 0, 'MBT': 0, 'complition': 0}


[None, None, None, None]

In [34]:
[print(vars(job)) for job in Jobs]

{'id': 0, 'release': 2, 'processing': 0, 'expected': 1, 'CV': 1, 'we': 3, 'alpha': None, 'ta': None, 'done_1': 0, 'MBT': 0, 'complition': 0}
{'id': 1, 'release': 3, 'processing': 1, 'expected': 3, 'CV': 1, 'we': 0, 'alpha': None, 'ta': None, 'done_1': 0, 'MBT': 0, 'complition': 0}
{'id': 2, 'release': 1, 'processing': 1, 'expected': 2, 'CV': 1, 'we': 1, 'alpha': None, 'ta': None, 'done_1': 0, 'MBT': 0, 'complition': 0}
{'id': 3, 'release': 1, 'processing': 2, 'expected': 3, 'CV': 1, 'we': 0, 'alpha': None, 'ta': None, 'done_1': 0, 'MBT': 0, 'complition': 0}


[None, None, None, None]

In [29]:
[print(vars(job)) for job in Jobs]

{'id': 0, 'release': 2, 'processing': 0, 'expected': 1, 'CV': 1, 'we': 2, 'alpha': None, 'ta': None, 'done_1': 0, 'MBT': 0, 'complition': 0}
{'id': 1, 'release': 3, 'processing': 0, 'expected': 1, 'CV': 1, 'we': 1, 'alpha': None, 'ta': None, 'done_1': 0, 'MBT': 0, 'complition': 0}
{'id': 2, 'release': 3, 'processing': 0, 'expected': 3, 'CV': 1, 'we': 0, 'alpha': None, 'ta': None, 'done_1': 0, 'MBT': 0, 'complition': 0}
{'id': 3, 'release': 1, 'processing': 0, 'expected': 0, 'CV': 1, 'we': 1, 'alpha': None, 'ta': None, 'done_1': 0, 'MBT': 0, 'complition': 0}


[None, None, None, None]

In [61]:
print(results)

[[]]


In [62]:
results=[3][3]
print(results)

IndexError: list index out of range